## **Proyecto final**
### **Laboratorio de Programación Científica para Ciencia de Datos MDS7202**

Integrante 1: Benjamín Angulo

Integrante 2: Vanessa González

### **1. Introducción**

Esta sección es una muy breve introducción con todo lo necesario para entender que hicieron en su proyecto.

Describir brevemente el problema planteado (¿Qué se intenta predecir?)

Describir brevemente los datos de entrada que les provee el problema.

Describir las métricas que utilizarán para evaluar los modelos generados. Elijan una métrica adecuada para el desarrollo del
proyecto según la tarea que deben resolver y la institución a la cuál será su contraparte y luego justifiquen su elección.

Considerando que los datos presentan desbalanceo y que el uso de la métrica 'accuracy' sería incorrecto, enfoquen su
elección en una de las métricas precision, recall o f1-score y en la clase que será evaluada.

[Escribir al final] Describir brevemente los modelos que usaron para resolver el problema (incluyendo las transformaciones
intermedias de datos).

[Escribir al final] Indicar si lograron resolver el problema a través de su modelo final. Indiquen además si creen que los
resultados de su mejor modelo son aceptables y como les fue con respecto al resto de los equipos.

Variables disponibles:

1. income: La lana que el equipo obtiene.
2. AliasMatch: Cuánto coinciden el nombre y el correo.
3. OldHoodMonths: Meses pasando el rato en la vieja casa.
4. NewCribMonths: Meses instalados en el nuevo lugar.
5. customer_age: Los años que ha estado el cliente en el juego.
6. DaysSinceJob: Días desde que se planeó el último gran golpe.
7. intended_balcon_amount: La lana destinada para el trabajo.
8. LootMethod: Cómo se va a mover la plata.
9. ZipHustle: Actividad de estafa en el código postal en las últimas 4 semanas.
10. Speed6h: Qué tan rápido se movieron en las últimas 6 horas.
11. Speed24h: Qué tan rápido se movieron en las últimas 24 horas.
12. Speed4w: Qué tan rápido se movieron en las últimas 4 semanas.
13. BankSpots8w: Número de bancos golpeados en las últimas 8 semanas.
14. DOBEmails4w: Correos diferentes usados con la misma fecha de nacimiento en las últimas 4 semanas.
15. JobStatus: ¿Cuál es la situación laboral del cliente?
16. RiskScore: Qué tan riesgoso cree el equipo que es el trabajo.
17. FreeMail: Si el correo proviene de un proveedor gratuito o no.
18. CribStatus: El tipo de vivienda donde está instalado el cliente.
19. HomePhoneCheck: Si el teléfono fijo está en orden.
20. CellPhoneCheck: Si el teléfono celular es legítimo.
21. BankMonths: Cuánto tiempo ha estado el cliente con su banco actual.
22. ExtraPlastic: Si el cliente tiene otras tarjetas de crédito.
23. CreditCap: El límite propuesto en el crédito.
24. ForeignHustle: Si el trabajo tiene un toque extranjero.
25. InfoSource: De dónde viene la información.
26. HustleMinutes: Cuánto tiempo ha estado el cliente en línea.
27. DeviceOS: El sistema operativo en el dispositivo.
28. AliveSession: Si la sesión sigue activa.
29. DeviceEmails8w: Número de correos únicos usados en el dispositivo en las últimas 8 semanas.
30. DeviceScams: Número de intentos de fraude desde el dispositivo.
31. HustleMonth: El mes en que se lleva a cabo el trabajo.

### **2. Modelos con Scikit-Learn**

In [9]:
# importamos librerías que se utilizarán a lo largo del proyecto
import pandas as pd
import numpy as np
from scipy import stats
from scipy.stats import norm
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.metrics import classification_report, precision_recall_curve, auc, roc_curve, recall_score
from sklearn.pipeline import Pipeline
from sklearn.tree import DecisionTreeClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
import time

import warnings
warnings.filterwarnings('ignore')

#### **2.1 Análisis Exploratorio de Datos**

En esta sección se realiza un análisis exploratorio de datos para investigar patrones, tendencias y relaciones en el conjunto de datos entregado. Para ello, primero se leen los archivos disponibles y se crea un dataframe que contenga tanto las features como la clase de cada cliente. Luego se exploran los nulos en los datos y el tipo de datos con que cuenta cada columna. Con respecto a los nulos, no hay datos nulos en ninguna columna, y con respecto a los tipos de datos se pueden encontrar columnas tanto categóricas (ej: JobStatus, DeviceOS, LootMethod) como numéricas (ej: CreditCap, Speed24h, AliasMatch). Los nombres de las columnas categóricas y numéricas son guardados en 2 listas para facilitar análisis posteriores y el preprocesamiento de los datos.


In [10]:
# lectura de archivos
X_t0 = pd.read_csv('X_t0', sep = ',')
y_t0 = pd.read_csv('y_t0', sep = ',')
y_t0 = y_t0[['is_mob']]
# dataframe con features y clase
df = X_t0.copy() 
df['is_mob'] = y_t0['is_mob']

In [37]:
# nulos por columna: no hay nulos
print(df.isnull().sum())

DaysSinceJob              0
CreditCap                 0
JobStatus                 0
Speed24h                  0
AliveSession              0
BankSpots8w               0
HustleMinutes             0
RiskScore                 0
AliasMatch                0
DeviceEmails8w            0
CribStatus                0
LootMethod                0
InfoSource                0
HustleMonth               0
ZipHustle                 0
Speed4w                   0
DeviceOS                  0
income                    0
FreeMail                  0
HomePhoneCheck            0
BankMonths                0
DOBEmails4w               0
ForeignHustle             0
DeviceScams               0
OldHoodMonths             0
intended_balcon_amount    0
NewCribMonths             0
Speed6h                   0
CellPhoneCheck            0
customer_age              0
ExtraPlastic              0
is_mob                    0
dtype: int64


In [38]:
# tipo de datos
print(df.dtypes) 

DaysSinceJob              float64
CreditCap                 float64
JobStatus                  object
Speed24h                  float64
AliveSession                int64
BankSpots8w                 int64
HustleMinutes             float64
RiskScore                   int64
AliasMatch                float64
DeviceEmails8w              int64
CribStatus                 object
LootMethod                 object
InfoSource                 object
HustleMonth                 int64
ZipHustle                   int64
Speed4w                   float64
DeviceOS                   object
income                    float64
FreeMail                    int64
HomePhoneCheck              int64
BankMonths                  int64
DOBEmails4w                 int64
ForeignHustle               int64
DeviceScams                 int64
OldHoodMonths               int64
intended_balcon_amount    float64
NewCribMonths               int64
Speed6h                   float64
CellPhoneCheck              int64
customer_age  

In [11]:
# columnas numéricas
columnas_numericas = ["DaysSinceJob", "CreditCap", "Speed24h", "AliveSession", "BankSpots8w", "HustleMinutes", "RiskScore", "AliasMatch", "DeviceEmails8w", "HustleMonth", "ZipHustle", "Speed4w", "income", "FreeMail",
                      "HomePhoneCheck", "BankMonths", "DOBEmails4w", "ForeignHustle", "OldHoodMonths", "intended_balcon_amount", "NewCribMonths", "Speed6h", "CellPhoneCheck", "customer_age", "ExtraPlastic"]
# columnas cateóricas
columnas_categoricas = ["JobStatus", "CribStatus", "LootMethod", "InfoSource", "DeviceOS"]

Adicionalmente, se visualiza un resumen de las estadísticas del dataframe, donde se puede notar que tanto el máximo como el mínimo de la columna DeviceScams son nulos, es decir, la columna solo tiene ceros y por ende no aporta información. Debido a ello, DeviceScams se elimina del dataframe.

In [40]:
# estadísticas generales
df.describe()

DaysSinceJob      CreditCap       Speed24h   AliveSession  \
count  3.970390e+05  397039.000000  397039.000000  397039.000000   
mean   1.194997e+00     521.162631    5570.712126       0.609026   
std    5.334243e+00     515.446406    1351.261338       0.487969   
min    4.036860e-09     190.000000    1517.555809       0.000000   
25%    7.218052e-03     200.000000    4602.212446       0.000000   
50%    1.538161e-02     200.000000    5485.225013       1.000000   
75%    2.737877e-02     990.000000    6625.724678       1.000000   
max    7.658148e+01    2100.000000    9502.725577       1.000000   

         BankSpots8w  HustleMinutes      RiskScore     AliasMatch  \
count  397039.000000  397039.000000  397039.000000  397039.000000   
mean      191.789630       8.393079     112.618186       0.514320   
std       462.968776       8.648661      72.456036       0.286733   
min         0.000000      -1.000000    -169.000000       0.000019   
25%         1.000000       3.622840      60.000000       0.258522   
50%        10.000000       5.535551     104.000000       0.523120   
75%        31.000000       9.808629     158.000000       0.769828   
max      2381.000000      83.213536     389.000000       0.999999   

       DeviceEmails8w    HustleMonth  ...  ForeignHustle  DeviceScams  \
count   397039.000000  397039.000000  ...  397039.000000     397039.0   
mean         1.031297       1.011432  ...       0.027604          0.0   
std          0.220586       0.823676  ...       0.163837          0.0   
min         -1.000000       0.000000  ...       0.000000          0.0   
25%          1.000000       0.000000  ...       0.000000          0.0   
50%          1.000000       1.000000  ...       0.000000          0.0   
75%          1.000000       2.000000  ...       0.000000          0.0   
max          2.000000       2.000000  ...       1.000000          0.0   

       OldHoodMonths  intended_balcon_amount  NewCribMonths        Speed6h  \
count  397039.000000           397039.000000  397039.000000  397039.000000   
mean       16.752354                9.254470      88.541015    6903.925002   
std        44.058472               20.251431      91.805720    3159.147744   
min        -1.000000              -13.202786      -1.000000     -80.690670   
25%        -1.000000               -1.153763      19.000000    4592.756809   
50%        -1.000000               -0.788469      53.000000    6823.830632   
75%        12.000000               12.655739     133.000000    8847.104551   
max       372.000000              112.956928     425.000000   16715.565404   

       CellPhoneCheck   customer_age   ExtraPlastic         is_mob  
count   397039.000000  397039.000000  397039.000000  397039.000000  
mean         0.876473      33.448452       0.184508       0.009813  
std          0.329041      12.160613       0.387899       0.098572  
min          0.000000      10.000000       0.000000       0.000000  
25%          1.000000      20.000000       0.000000       0.000000  
50%          1.000000      30.000000       0.000000       0.000000  
75%          1.000000      40.000000       0.000000       0.000000  
max          1.000000      90.000000       1.000000       1.000000  

[8 rows x 27 columns]

In [41]:
print(max(df['DeviceScams']), min(df['DeviceScams']))

0 0


In [12]:
# se elimina la columna DeviceScams ya que todos sus valores son iguales a 0 por lo que no aporta información 
df = df.drop('DeviceScams', axis=1)

##### 2.1.1 Desbalanceo de clases

Un primer punto del análisis exploratorio consiste en evaluar qué tan balanceadas están las clases. Para ello,  creamos los dataframes mob y not_mob con los clientes fraudulentos y no fraudulentos, respectivamente. Luego, graficamos el número de muestras de cada clase. De acuerdo al gráfico, en los datos disponibles hay 3.896 clientes fraudulentos y 393.143 clientes no fraudulentos, es decir, las clases están muy desbalanceadas y los casos fraudulentos están subrepresentados.

In [9]:
# separamos los casos fraudulentos y no fraudulentos
mob = df[df['is_mob'] == 1]
not_mob = df[df['is_mob'] == 0]

In [10]:
# desbalanceo de clases
fig = go.Figure()
fig.add_trace(go.Bar(x=['Muestra Mob'], y=[len(mob)], name='Fraudulento', marker_color='orange'))
fig.add_trace(go.Bar( x=['Muestra Not Mob'], y=[len(not_mob)], name='No fraudulento', marker_color='blue'))
fig.update_layout(title='Número de muestras para casos fraudulentos y no fraudulentos', xaxis_title='Tipo de muestra', yaxis_title='Conteo', barmode='group', width=600, height=400)
fig.show()

##### 2.1.1 Variables numéricas

Para estudiar las variables numéricas, se decide primero graficar la correlación que existe entre ellas, además de la correlación que tienen con la clase. De acuerdo a ello, se puede notar que existen algunas correlaciones notorias:
* HustleMonth y Speed4w tienen una correlación muy negativa, es decir, cuando una aumenta, la otra disminuye significativamente.
* customer_age y DOBEmails4w también tienen una correlación bastante negativa, cuando una aumenta, la otra disminuye significativamente.
* CreditCap y RiskScore tienen una alta correlación positiva, por lo que cuando una de ellas aumenta, la otra también lo hace.

In [ ]:
correlation_matrix = df[columnas_numericas+['is_mob']].corr()
fig = make_subplots(rows=1, cols=1)
heatmap = go.Heatmap(z=correlation_matrix.values, x=correlation_matrix.columns, y=correlation_matrix.columns, colorscale='Viridis')
fig.add_trace(heatmap)
fig.update_layout(title_text='Matriz de correlación para columnas numéricas', height=800, width=800, xaxis_title='Variable', yaxis_title='Variable')
fig.show()

Ahora, se decide estudiar qué ocurre para las variables OldHoodMonths y NewCribMonths para clientes fraudulentos y no fraudulentos. Para estas variables, es importante notar que existen muchos valores iguales a -1, lo que puede indicar datos faltantes o no disponibles, pues un cliente no puede estar -1 meses en una propiedad. Debido a ello, se cuentan los clientes donde las variables toman un valor de -1 y se grafican las distribuciones de ambas variables tomando solo los valores positivos.

De los 397.039 clientes totales, 280.119 no presentan información en OldHoodMonths, y 1.595 no presentan información en NewCribMonths. Luego, explorando los valores positivos de ambas variables, se tiene que en el caso de OldHoodMonths la distribución es similar para todos los clientes, no obstante, en el caso de NewCribMonths la distribución para casos fraudulentos se mueve hacia la derecha. Es decir, los clientes fraudulentos tienden a llevar más tiempo en su nueva residencia. Esto puede tener relación con varios factores, como que los clientes fraudulentos una vez que se mudan a una nueva residencia, opten por quedarse más tiempo para reducir el riesgo de ser detectados.

Considerando la gran cantidad de datos faltantes en OldHoodMonths y que las distribuciones en ambas clases son muy similares, puede que esta variable no resulte útil al momento de clasificar.

In [ ]:
# Para estas variables hay muchos casos donde el valor es -1, lo que podría indicar que hay datos faltantes o no disponibles (el cliente no puede estar -1 meses en una propiedad)
print('nº de clientes totales: ', len(df))
print('nº de clientes sin información en OldHoodMonths: ', len(df[df['OldHoodMonths'] == -1]))
print('nº de clientes sin información en NewCribMonths: ', len(df[df['NewCribMonths'] == -1]))

# Casos fraudulentos
fig = go.Figure()
fig.add_trace(go.Histogram(x=mob[mob['OldHoodMonths'] > 0]['OldHoodMonths'], name='OldHoodMonths', nbinsx=30, opacity=0.3,  marker_color='blue'))
fig.add_trace(go.Histogram(x=mob[mob['NewCribMonths'] > 0 ]['NewCribMonths'], name='NewCribMonths', nbinsx=30, opacity=0.3, marker_color='orange'))
fig.update_layout(title='Distribución de OldHoodMonths y NewCribMonths para casos fraudulentos', xaxis_title='Meses', yaxis_title='Frecuencia', barmode='overlay', width=800, height=400)
fig.show()

# Casos no fraudulentos
fig = go.Figure()
fig.add_trace(go.Histogram(x=not_mob[not_mob['OldHoodMonths'] > 0]['OldHoodMonths'], name='OldHoodMonths', nbinsx=30, opacity=0.3, marker_color='blue'))
fig.add_trace(go.Histogram(x=not_mob[not_mob['NewCribMonths'] > 0 ]['NewCribMonths'], name='NewCribMonths', nbinsx=30, opacity=0.3, marker_color='orange'))
fig.update_layout(title='Distribución de OldHoodMonths y NewCribMonths para casos no fraudulentos', xaxis_title='Meses', yaxis_title='Frecuencia', barmode='overlay', width=800, height=400)
fig.show()

Por otro lado, se grafican las distribuciones de Speed6h, Speed24h y Speed4w, que son variables que representan la velocidad o frecuencia de actividad de un cliente en las últimas 6 horas, últimas 24 horas y últimas 4 semanas, respectivamente. En los gráficos se puede notar que las distribuciones de speed se ven muy similares para clientes fraudulentos y no fraudulentos, solo que en los no fraudulentos hay un peak muy notable para Speed4w en 5400-5600, lo cual podría indicar un comportamiento que es más común entre los clientes no fraudulentos que entre los fraudulentos. 

In [ ]:
# speed: fraudulentos
fig = go.Figure()
fig.add_trace(go.Histogram(x=mob['Speed6h'], name='Speed6h', nbinsx=30, opacity=0.3, marker_color='blue'))
fig.add_trace(go.Histogram(x=mob['Speed24h'], name='Speed24h', nbinsx=30, opacity=0.3, marker_color='orange'))
fig.add_trace(go.Histogram(x=mob['Speed4w'], name='Speed4w', nbinsx=30,  opacity=0.3, marker_color='green'))
fig.update_layout(title='Distribución de speed para casos fraudulentos', xaxis_title='Speed', yaxis_title='Frecuencia', barmode='overlay',  width=800, height=400)
fig.show()

# speed: no fraudulentos
fig = go.Figure()
fig.add_trace(go.Histogram(x=not_mob['Speed6h'], name='Speed6h', nbinsx=30, opacity=0.3, marker_color='blue'))
fig.add_trace(go.Histogram(x=not_mob['Speed24h'], name='Speed24h', nbinsx=30, opacity=0.3, marker_color='orange'))
fig.add_trace(go.Histogram(x=not_mob['Speed4w'], name='Speed4w', nbinsx=30,  opacity=0.3, marker_color='green'))
fig.update_layout(title='Distribución de speed para casos no fraudulentos', xaxis_title='Speed', yaxis_title='Frecuencia', barmode='overlay',  width=800, height=400)
fig.show()

A continuación, se comparan las distribuciones de varias variables numéricas, pero dado el desbalanceo de las clases sus valores son normalizados por el número de clientes de la clase correspondiente. Esto permite superponer las distribuciones de ambas clases sin que los casos fraudulentos sean difíciles de visualizar. El procedimiento se lleva a cabo con la función hist_norm_freq.

In [17]:
def hist_norm_freq(variable, variable_name, xlabel, num_bins = 30):

    mob_hist, mob_bins = np.histogram(mob[variable], bins=num_bins, density=False)
    mob_bin_centers = 0.5 * (mob_bins[1:] + mob_bins[:-1])
    mob_normalized = mob_hist / len(mob)

    not_mob_hist, not_mob_bins = np.histogram(not_mob[variable], bins=num_bins, density=False)
    not_mob_bin_centers = 0.5 * (not_mob_bins[1:] + not_mob_bins[:-1])
    not_mob_normalized = not_mob_hist / len(not_mob)

    fig = go.Figure()
    fig.add_trace(go.Bar(x=mob_bin_centers, y=mob_normalized, name='Fraudulento', marker_color='orange', opacity=0.3))
    fig.add_trace(go.Bar(x=not_mob_bin_centers, y=not_mob_normalized, name='No fraudulento', marker_color='blue', opacity=0.3))
    fig.update_layout(title=variable_name + ' (Fraudulento vs No fraudulento)', xaxis_title=xlabel, yaxis_title='Frecuencia normalizada', barmode='overlay', width=800, height=400)
    fig.show()

La primera variable visualizada es AliasMatch, que representa el grado de coincidencia entre el nombre del cliente y su dirección de correo electrónico. De acuerdo a lo observado en el gráfico, para los casos fraudulentos hay una clara concentración en valores más bajos de AliasMatch, es decir, para ese tipo de cliente la coincidencia entre el nombre y el correo es menor. Lo anterior puede tener relación son que los defraudadores usan alias o correos electrónicos que no están relacionados con sus nombres reales para evitar ser detectados.

In [ ]:
hist_norm_freq('AliasMatch', 'AliasMatch', 'AliasMatch')

Ahora, analizamos DOEmails4w, que representa el número de direcciones de correo electrónico diferentes que han sido utilizadas con la misma fecha de nacimiento en las últimas 4 semanas. En este caso, para los clientes fraudulentos la distribución se mueve hacia la izquierda, es decir, tienden a haber menos correos con la misma fecha de nacimiento. Esto puede relacionarse con muchos factores, por ejemplo, existe la posibilidad de que los clientes fraudulentos estén utilizando diferentes identidades con distintas fechas de nacimiento para evitar ser detectados, pues con ello se evita el uso repetitivo de la misma fecha de nacimiento.

In [ ]:
hist_norm_freq('DOBEmails4w', 'Correos diferentes con la misma fecha de nacimiento', 'nº de correos diferentes')

Se sigue con ZipHustle, que representa la actividad de estafa en el código postal en las últimas 4 semanas. Para esta variable, las distribuciones de cada clase son idénticas, esto sugiere que la actividad de fraude en el código postal no es un factor discriminante entre estas dos clases.

In [ ]:
hist_norm_freq('ZipHustle', 'Actividad de estafa en el código postal', 'Actividad de estafa')

Por otro lado, se analiza BankMonths, que representa la cantidad de tiempo, en meses, que un cliente ha estado con su banco actual. En este caso se debe considerar que, similar a OldHoodMonths y NewCribMonths, existen valores iguales a -1, que pueden deberse a datos faltantes o no disponibles. De un total de 397.039 clientes, 97.716 presentan un valor de BankMonths igual a -1. 

Analizando solo los valores positivos, se tiene que las distribuciones son similares para ambas clases, no obstante, hay una proporción mayor de clientes fraudulentos en torno a los 30 meses, y una proporción mayor de clientes no fraudulentos en torno a 0-1 meses. Esto sugiere que el tiempo que un cliente ha estado con el banco no es un diferenciador fuerte entre clientes fraudulentos y no fraudulentos, aunque específicamente se puede notar que muchos clientes nuevos son legítimos.

In [25]:
print('nº de clientes totales: ', len(df))
print('nº de clientes sin información en BankMonths: ', len(df[df['BankMonths'] == -1]))

nº de clientes totales:  397039
nº de clientes sin información en BankMonths:  97716


In [ ]:
hist_norm_freq('BankMonths', 'Meses que el cliente ha estado con su banco actual', 'Meses en el banco actual')

En cuanto a CreditCap, esta representa el límite de crédito propuesto para un cliente. De acuerdo al gráfico, el límite de crédito suele ser un poco más bajo para clientes no fraudulentos, lo que puede tener relación con que clientes fraudulentos busquen límites de crédito altos para maximizar su beneficio antes de que se detecte el fraude. De hecho, en 2000 prácticamente todos los clientes son fraudulentos, ya que puede tratarse de un valor inusualmente alto.

In [ ]:
hist_norm_freq('CreditCap', 'Límite propuesto en el crédito', 'Límite propuesto en el crédito', num_bins=df['CreditCap'].nunique())

Por otra parte, customer_age indica cuántos años ha estado el cliente involucrado en las actividades financieras, lo que puede reflejar su experiencia y familiaridad con el sistema. En este caso, se tiene que los clientes fraudulentos presentan una leve tendencia a llevar más años. Lo anterior podría tener relación con que, por ejemplo, los clientes con más antigüedad pueden haber adquirido una comprensión más profunda de cómo funcionan los sistemas financieros, lo que les permite ejecutar fraudes de manera más efectiva.

In [ ]:
hist_norm_freq('customer_age', 'Años que lleva el cliente en el banco', 'Años', num_bins=df['customer_age'].nunique())

##### 2.1.3 Variables categóricas

En esta sección se exploran variables categóricas, para lo cual se utiliza la función dist_categoric_variable, que hace un gráfico de barras por clase con la distribución de la variable. Se elige esto en lugar de barras apiladas dada la gran diferencia en el número de clientes por clase.

In [35]:
def dist_categoric_variable(variable, variable_name):
    # ocurrencias de cada categoría de la variable en 'mob'
    mob_counts = mob[variable].value_counts().reset_index()
    mob_counts.columns = [variable, 'Count']

    # ocurrencias de cada categoría de la variable en 'not_mob'
    not_mob_counts = not_mob[variable].value_counts().reset_index()
    not_mob_counts.columns = [variable, 'Count']

    fig = make_subplots(rows=1, cols=2, subplot_titles=('Clientes fraudulentos', 'Clientes no fraudulentos'), specs=[[{'secondary_y': False}, {'secondary_y': False}]])
    fig.add_trace(go.Bar(x=mob_counts[variable], y=mob_counts['Count'], name='Fraudulento', marker_color='orange'), row=1, col=1)
    fig.add_trace(go.Bar(x=not_mob_counts[variable], y=not_mob_counts['Count'], name='No fraudulento', marker_color='blue'), row=1, col=2)
    fig.update_layout(title=f'Distribución de {variable_name}', width=1100, height=400)
    fig.update_xaxes(title_text=variable_name, row=1, col=1)
    fig.update_xaxes(title_text=variable_name, row=1, col=2)
    fig.update_yaxes(title_text='Conteo', row=1, col=1)
    fig.update_yaxes(title_text='Conteo', row=1, col=2)
    fig.show()

Para empezar, se explora JobStatus, que indica la situación laboral del cliente mediante dos letras ('CB', 'CA', 'CC', 'CF', 'CD', 'CE' o 'CG'). De acuerdo a lo observado, siempre existe una gran predominancia de 'CA', y existen pequeñas diferencia en la presencia de otros valores como 'CC' y 'CB'.

In [ ]:
dist_categoric_variable('JobStatus', 'JobStatus')

Por su parte, CribStatus es una variable que indica el tipo de vivienda en la que reside el cliente mediante 2 letras también ('BC', 'BE', 'BD', 'BA', 'BB', 'BF', 'BG'). Para esta variable si hay grandes diferencias en los valores predominantes, ya que para clientes fraudulentos predomina 'BA', seguido de 'BC' y 'BB', mientras en clientes no fraudulentos predomina 'BC', seguido de 'BB' y 'BE'.

In [ ]:
dist_categoric_variable('CribStatus', 'CribStatus')

Por otro lado, se tiene LootMethod, que describe la estrategia o método que utiliza el cliente para realizar transacciones o manejar su dinero mediante 2 letras ('AA', 'AB', 'AC', 'AD', 'AE'). Esto también presenta diferencias importantes entre una clase y otra, ya que para clientes fraudulentos predominan 'AC' y 'AB' de manera notoria, mientras 'AE' no tiene ocurrencias. En cambio, en los clientes no fraudulentos predominan 'AB' y 'AA', seguidos de cerca por 'AC'.

In [ ]:
dist_categoric_variable('LootMethod', 'LootMethod')

Para estudiar el sistema operativo del dispositivo que utiliza el cliente para realizar transacciones o acceder a servicios financieros se visualiza DeviceOS, que cuenta con los valores 'linux', 'other', 'windows', 'x11' y 'macintosh'. Aquí se encuentran diferencias notables, ya que en los clientes no fraudulentos predomina 'linux', seguido de cerca por 'other' y 'windows', mientras en los clientes fraudulentos predomina 'windows' muy por sobre las otras opciones. Esto podría sugerir que Windows es más utilizado en contextos de fraude, tal vez por su accesibilidad o la prevalencia de software malicioso. No obstante, también se debe considerar que Windows es uno de los sistemas operativos más utilizados en el mundo, lo que puede llevar a una mayor cantidad de usuarios fraudulentos simplemente por su popularidad. Asimismo, los clientes que utilizan Linux pueden tener un nivel de competencia técnica que los hace menos propensos a realizar fraudes, o pueden estar más informados sobre seguridad.

In [ ]:
dist_categoric_variable('DeviceOS', 'DeviceOS')

En cuanto a InfoSource, es una variable que indica la fuente de información de la que provienen los datos del cliente. De acuerdo a lo observado, no aporta mucha información relevante, ya que en cualquier clase la predominancia de 'INTERNET' es muy clara.

In [ ]:
dist_categoric_variable('InfoSource', 'InfoSource')

#### **2.2 Pre-Procesamiento de datos**

Como se mencionó anteriormente, existen tanto variables numéricas como categóricas, donde ninguna de ellas presenta valores nulos. No obstante, hay variables que por lógica deben tomar valores mayores a 0 y cuentan con una gran cantidad de valores iguales a -1, los cuales podrían representar datos faltantes o no disponibles, y por ende, deben ser imputados.

Las columnas numéricas que presentan el problema anterior son: HustleMinutes, DeviceEmails8w, BankMonths, OldHoodMonths y NewCribMonths. Debido a ello, sus valores iguales a -1 se imputan reemplazándolos por la mediana de los valores de la columna. Se escoge este enfoque de imputación porque la mediana es robusta frente a valores atípicos que se pueden presentan dada la variabilidad de los datos. Además, posterior a la imputación se escalan los datos con un StandardScaler, y la imputación por mediana no distorsiona los valores escalados. En cuanto a las variables categóricas, estas se pre-procesan utilizando un one-hot encoding. 

Una vez listo el column transformer para el pre-procesamiento de variables, se procede a dividir los datos disponibles en un conjunto de entrenamiento y uno de prueba, de manera que el conjunto de prueba contenga el 30% de las muestras.


In [44]:
def print_min_values(df):
    for column in df.columns:
        min_value = df[column].min()
        print(f"{column}: {min_value}")

print_min_values(df[columnas_numericas])

DaysSinceJob: 4.036859788721786e-09
CreditCap: 190.0
Speed24h: 1517.5558094221874
AliveSession: 0
BankSpots8w: 0
HustleMinutes: -1.0
RiskScore: -169
AliasMatch: 1.939656590466133e-05
DeviceEmails8w: -1
HustleMonth: 0
ZipHustle: 2
Speed4w: 2975.540227165919
income: 0.1
FreeMail: 0
HomePhoneCheck: 0
BankMonths: -1
DOBEmails4w: 0
ForeignHustle: 0
OldHoodMonths: -1
intended_balcon_amount: -13.202786124951324
NewCribMonths: -1
Speed6h: -80.69066966650415
CellPhoneCheck: 0
customer_age: 10
ExtraPlastic: 0


In [45]:
print('nº de clientes totales: ', len(df))
print('nº de clientes sin información en HustleMinutes: ', len(df[df['HustleMinutes'] == -1]))
print('nº de clientes sin información en DeviceEmails8w: ', len(df[df['DeviceEmails8w'] == -1]))
print('nº de clientes sin información en BankMonths: ', len(df[df['BankMonths'] == -1]))
print('nº de clientes sin información en OldHoodMonths: ', len(df[df['OldHoodMonths'] == -1]))
print('nº de clientes sin información en NewCribMonths: ', len(df[df['NewCribMonths'] == -1]))

nº de clientes totales:  397039
nº de clientes sin información en HustleMinutes:  758
nº de clientes sin información en DeviceEmails8w:  184
nº de clientes sin información en BankMonths:  97716
nº de clientes sin información en OldHoodMonths:  280119
nº de clientes sin información en NewCribMonths:  1595


In [34]:
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.impute import SimpleImputer

columnas_a_imputar = ['HustleMinutes', 'DeviceEmails8w', 'BankMonths', 'OldHoodMonths', 'NewCribMonths']

impute_and_scale_pipeline = Pipeline(steps=[
    ('impute', SimpleImputer(missing_values=-1, strategy='median')),
    ('scale', StandardScaler())
])

# Definir el ColumnTransformer
col_transformer = ColumnTransformer(
    transformers=[
        ('impute_and_scale', impute_and_scale_pipeline, columnas_a_imputar),
        ('num', StandardScaler(), list(set(columnas_numericas)-set(columnas_a_imputar))),
        ('cat', OneHotEncoder(), columnas_categoricas)
    ])

In [35]:
from sklearn.model_selection import train_test_split

X = df.drop('is_mob', axis=1)  
y = df['is_mob']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42, stratify=y)

#### **2.3 Baseline**

En esta sección se aborda el problema utilizando el modelo más básico posible, que en este caso corresponde a un DummyClassifier que realiza predicciones de manera aleatoria o utilizando estrategias simples, sin intentar aprender de los datos. Para evaluar su desempeño se imprime su classification_report, y también se grafican las curvas precision-recall y ROC, obteniendo el área bajo la curva. Adicionalmente de define una función que permite visualizar la matriz de confusión correspondiente.

Para el DummyClassifier, el classification_report muestra un rendimiento desigual del modelo, donde la clase 0 (no fraudulento) presenta excelentes métricas con una precisión del 99%, recall del 100% y un F1-score de 1.00, gracias a su alto soporte (117.943 muestras). En contraste, la clase 1 (fraudulento) presenta resultados muy pobres, con una precision, recall y F1-score de 0.00, lo que indica que el modelo no identifica correctamente esta clase minoritaria (1.169 muestras). Aunque la precisión global es alta (99%), esto sugiere un problema de desbalance en las clases, lo que limita la efectividad del modelo en tareas que requieren una clasificación adecuada de ambas clases.

Las curvas de precisión-recall y ROC muestran un rendimiento del modelo similar al de un clasificador aleatorio, representándose como líneas diagonales. Un área bajo la curva (AUC) de 0.5 en ambos casos indica que el modelo no es capaz de distinguir entre las clases de manera efectiva, lo que refuerza los resultados previos del classification_report, donde la clase minoritaria no fue identificada correctamente.

In [36]:
def plot_pr_roc(y_test, y_probs):

    precision, recall, pr_thresholds = precision_recall_curve(y_test, y_probs) # calcular las métricas de precisión y recall para la curva PR
    auc_pr = auc(recall, precision)

    fpr, tpr, roc_thresholds = roc_curve(y_test, y_probs) # Calcular las métricas para la curva ROC
    auc_roc = auc(fpr, tpr)

    fig = make_subplots(rows=1, cols=2, subplot_titles=('Curva de Precision-Recall', 'Curva ROC'))
    fig.add_trace(go.Scatter(x=recall, y=precision, mode='lines', name=f'Curva PR (AUC = {auc_pr:.2f})'), row=1, col=1)
    fig.add_trace(go.Scatter(x=fpr, y=tpr, mode='lines', name=f'Curva ROC (AUC = {auc_roc:.2f})'), row=1, col=2)
    fig.update_layout(title='Curvas de Precision-Recall y ROC', width=1100, height=400)
    fig.update_xaxes(title_text='Recall', row=1, col=1)
    fig.update_yaxes(title_text='Precision', row=1, col=1)
    fig.update_xaxes(title_text='False Positive Rate', row=1, col=2)
    fig.update_yaxes(title_text='True Positive Rate', row=1, col=2)
    fig.show()

from sklearn.metrics import confusion_matrix

def plot_confusion_matrix(y_test, y_pred):

    cm = confusion_matrix(y_test, y_pred)
    cm_df = pd.DataFrame(cm, index=['No fraudulento', 'Fraudulento'], columns=['No fraudulento', 'Fraudulento'])

    fig = go.Figure(data=go.Heatmap(z=cm_df.values, x=cm_df.columns, y=cm_df.index, colorscale='Viridis', text=cm_df.values, texttemplate="%{text}", textfont={"size": 20}, hoverinfo="text",))
    fig.update_layout( title='Matriz de confusión', xaxis_title='Predicted label', yaxis_title='True label', xaxis=dict(tickmode='linear'), yaxis=dict(tickmode='linear'), showlegend=False, width=500, height=400)
    fig.show()

In [37]:
from sklearn.dummy import DummyClassifier

dummy_pipeline = Pipeline([("transform", col_transformer), 
                     ("classifier", DummyClassifier())])

dummy_pipeline.fit(X_train, y_train)

pred = dummy_pipeline.predict(X_test)

print(classification_report(y_test, pred))

plot_pr_roc(y_test, dummy_pipeline.predict_proba(X_test)[:, 1])

              precision    recall  f1-score   support

           0       0.99      1.00      1.00    117943
           1       0.00      0.00      0.00      1169

    accuracy                           0.99    119112
   macro avg       0.50      0.50      0.50    119112
weighted avg       0.98      0.99      0.99    119112



#### **2.4 Modelos de ML**

En esta sección se prueban 3 clasificadores distintos al modelo baseline, explicando las diferencias entre ellos y los hiperparámetros con los que cuentan. Estos clasificadores son:

* Decision Tree 
* XGBoost
* LightGBM

En el caso de Decision Tree, este es un modelo de clasificación que utiliza un árbol de decisión para predecir la clase de una observación. Este método divide los datos en subconjuntos basándose en características de entrada, creando una estructura de árbol que facilita la toma de decisiones. Algunos de los parámetros importantes que se pueden ajustar en este clasificador son:

* criterion: Función utilizada para medir la calidad de una división.
* max_depth: Profundidad máxima del árbol. Limitar la profundidad puede ayudar a evitar el sobreajuste.
* min_samples_split: Número mínimo de muestras requeridas para dividir un nodo.
* min_samples_leaf: Número mínimo de muestras que debe tener un nodo hoja. Ayuda a evitar el sobreajuste al requerir que los nodos hoja contengan suficientes ejemplos.
* max_features: Número de características a considerar al buscar la mejor división.
* class_weight: Permite ajustar la importancia de las clases, útil en problemas de desbalance.

Por su parte, XGBoost es un modelo de clasificación basado en el algoritmo de Gradient Boosting, que utiliza árboles de decisión como modelos base. Algunos de sus parámetros importantes son:

* objective: Función objetivo a optimizar. Para clasificación binaria, comúnmente se usa 'binary:logistic'.
* eval_metric: Métrica para evaluar el rendimiento del modelo durante el entrenamiento. Aquí, "logloss" se usa para medir la pérdida logarítmica, que es adecuada para clasificación.
* booster: Tipo de modelo a usar (árboles de decisión, modelos lineales, etc.).
* lambda: Regularización L2. Controla la complejidad del modelo al penalizar grandes coeficientes, ayudando a evitar el sobreajuste.
* alpha: Regularización L1. Similar a lambda, pero penaliza la suma de los valores absolutos de los coeficientes. 
* learning_rate o eta: Tasa de aprendizaje que controla el paso del optimizador. Valores más bajos suelen dar mejor rendimiento, pero requieren más árboles.

Y por último, LightGBM es un modelo de clasificación basado en LightGBM, que es una implementación eficiente de Gradient Boosting que se enfoca en la velocidad y el uso de memoria. Algunos de sus parámetros son:

* learning_rate: Tasa de aprendizaje que determina el impacto de cada árbol. Valores bajos requieren más árboles para un buen rendimiento.
* n_estimators: Número de árboles a construir. Aumentar este número puede mejorar el ajuste, pero puede llevar al sobreajuste.
* max_depth: Profundidad máxima del árbol. Limitar la profundidad ayuda a evitar el sobreajuste.
* num_leaves: Número máximo de hojas por árbol. Un mayor número de hojas puede mejorar el ajuste, pero también aumenta el riesgo de sobreajuste.

Entre los 3 modelos utilizados, DecisionTreeClassifier es fácil de interpretar y rápido de entrenar, pero es propenso al sobreajuste. XGBClassifier ofrece alta precisión y rendimiento utilizando boosting, aunque es más complejo y requiere más recursos. LGBMClassifier es similar a XGBoost en precisión pero más rápido y eficiente en memoria, ideal para grandes volúmenes de datos y entrenamiento rápido. A continuación, se presentarán los resultados obtenidos con cada uno, sin optimizar sus parámetros.

In [38]:
# clasificadores
from sklearn.tree import DecisionTreeClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier

# metricas
from sklearn.metrics import recall_score, classification_report
import time

Para Decision Tree, este muestra altos precision y recall para la clase no fraudulenta, con valores de 0.99 en ambas métricas, lo que indica que el modelo identifica correctamente la mayoría de los clientes no fraudulentos. Sin embargo, la precision y recall para la clase fraudulenta son extremadamente bajas, ambas en torno a 0.07 y 0.08 respectivamente, lo que refleja que el modelo casi no logra identificar a los clientes fraudulentos. La f1-score global del modelo es alta, alcanzando un 0.98, pero esto es engañoso debido al fuerte desequilibrio de clases, donde la mayoría de los clientes son no fraudulentos. 

Por su parte, el área bajo la curva (AUC) precision-recall es 0.08, lo cual es muy bajo y sugiere que el modelo tiene un rendimiento pobre en la identificación de clientes fraudulentos. Por otro lado, el AUC de la curva ROC es 0.53, apenas mejor que el azar. Y por último, este modelo requiere alrededor de 13 a 15 segundos para entrenar.

In [ ]:
tree_pipeline = Pipeline([("transform", col_transformer), 
                     ("tree", DecisionTreeClassifier(criterion="entropy", random_state=152))])

tiempo_inicio_entrenamiento = time.time()
tree_pipeline.fit(X_train, y_train)
tiempo_fin_entrenamiento = time.time()
y_pred = tree_pipeline.predict(X_test)

print(classification_report(y_test, y_pred))
print('Tiempo: ' + str(np.round(tiempo_fin_entrenamiento - tiempo_inicio_entrenamiento, 2)) + ' [s]')
plot_pr_roc(y_test, tree_pipeline.predict_proba(X_test)[:, 1])

Pasando al clasificador XGBoost, su classification_report indica que presenta una alta precisión para la clase no fraudulenta (0.99) y una precisión moderada para la clase fraudulenta (0.39). Sin embargo, recall para la clase fraudulenta es extremadamente bajo (0.03), lo que significa que el modelo identifica correctamente muy pocos casos de fraude. Esto resulta en un F1-score bajo para la clase fraudulenta (0.06). La exactitud general del modelo es alta (0.99), pero está sesgada debido al predominio de la clase no fraudulenta. El promedio macro de precision, recall y F1-score son 0.69, 0.52 y 0.53 respectivamente, reflejando una mejora respecto al modelo de árbol de decisión, pero aún insuficiente en la detección de fraudes.

Por otro lado, para este modelo el área bajo la curva (AUC) precision-recall es 0.11, lo que es bastante bajo y sugiere que el modelo no maneja bien el equilibrio entre precisión y recall para la clase minoritaria. En contraste, el AUC de la curva ROC es 0.86, lo que indica que el modelo tiene una buena capacidad para distinguir entre clases fraudulentas y no fraudulentas en un sentido general. No obstante, hay que recordar el sego que existe por el desbalanceo de clases, por lo que la curva precision-recall es mucho más informativa.

Por último, XGBoost requiere alrededor de 4 a 6 segundos para entrenar, lo que es significativamente mejor que lo requerido por Decision Tree.

In [ ]:
xgb_pipeline = Pipeline([("transform", col_transformer),
                        ("classifier", XGBClassifier(random_state=152))])

tiempo_inicio_entrenamiento = time.time()
xgb_pipeline.fit(X_train, y_train)
tiempo_fin_entrenamiento = time.time()
y_pred = xgb_pipeline.predict(X_test)

print(classification_report(y_test, y_pred))
print('Tiempo: ' + str(np.round(tiempo_fin_entrenamiento - tiempo_inicio_entrenamiento, 2)) + ' [s]')
plot_pr_roc(y_test, xgb_pipeline.predict_proba(X_test)[:, 1])

Pasando al tercer modelo, los resultados del modelo LightGBM muestran una alta precisión para la clase no fraudulenta (0.99) y una precisión moderada para la clase fraudulenta (0.35). Sin embargo, el recall para la clase fraudulenta es bajo (0.05), lo que indica que el modelo identifica correctamente solo una pequeña fracción de los casos de fraude. Esto resulta en un F1-score bajo para la clase fraudulenta (0.08).

La exactitud general del modelo es alta (0.99), reflejando un sesgo hacia la clase no fraudulenta debido al desequilibrio de clases. El promedio macro de precisión, recuperación y F1-score son 0.67, 0.52 y 0.54 respectivamente, sugiriendo una ligera mejora respecto a los modelos anteriores, pero aún insuficiente en la detección de fraudes. Respecto al tiempo de entrenamiento, suele estar entre 4 y 5 segundos, lo que indica que el modelo es eficiente en términos de tiempo de entrenamiento si se le compara con los 2 modelos anteriores.

In [ ]:
lgbm_pipeline = Pipeline([("transform", col_transformer),
                        ("classifier", LGBMClassifier(random_state=152))])

tiempo_inicio_entrenamiento = time.time()
lgbm_pipeline.fit(X_train, y_train)
tiempo_fin_entrenamiento = time.time()
y_pred = lgbm_pipeline.predict(X_test)

print(classification_report(y_test, y_pred))
print('Tiempo: ' + str(np.round(tiempo_fin_entrenamiento - tiempo_inicio_entrenamiento, 2)) + ' [s]')
plot_pr_roc(y_test, lgbm_pipeline.predict_proba(X_test)[:, 1])

En resumen, los 3 modelos presentan mejores resultados que el azar, y entre ellos, XGBoost y LightGBM son mucho mejores que DecisionTree en términos de sus métricas y del área bajo la curva de precision-recall. Ahora, entre XGBoost y LightGBM, se tiene que LightGBM tiene un recall ligeramente mejor (0.04) que XGBoost (0.04) para la clase fraudulenta, aunque con una precisión ligeramente inferior (0.30 versus 0.36). En cuanto a otras métricas, el f1-score es ligeramente mayor en LightGBM (0.07 versus 0.06). 

Tomando el cuenta las diferencias anteriores, que XGBoost y LightGBM demoran casi el mismo tiempo en entrenar y que XGBoost tiene un mejor desempeño general, se elige este último para las siguientes secciones del proyecto.

#### **2.5 Optimización de modelos**

Acá se explica la forma en la que se realizó la optimización de los modelos. Hiperparámetros ocupados.
Deberán usar Optuna para tunear hiperparámetros. Además de crear pipelines para cada uno de los modelos.

Algunas ideas para mejorar el rendimiento de sus modelos:

Técnicas de selección de atributos.

Variar el imputador de datos, en caso de usarlo.

En esta sección se optimiza el modelo elegido anteriormente, es decir, XGBoost. Para ello se se hace uso de Optuna, que permite ajustar hiperparámetros buscando dentro de un rango definido. 


In [ ]:
pip install imbalanced-learn

In [66]:
import optuna
from optuna.samplers import TPESampler
from sklearn.metrics import accuracy_score
from sklearn.feature_selection import RFE
#from imblearn.over_sampling import SMOTE
#from imblearn.pipeline import Pipeline as ImbPipeline

def objective_xgb(trial):
    param = {
        "verbosity": 0,
        "objective": "binary:logistic",
        "eval_metric": "logloss",
        "booster": trial.suggest_categorical("booster", ["gbtree", "gblinear", "dart"]),
        "lambda": trial.suggest_loguniform("lambda", 1e-4, 10),
        "alpha": trial.suggest_loguniform("alpha", 1e-4, 10),
        "max_depth": trial.suggest_int("max_depth", 1, 10),
        "eta": trial.suggest_loguniform("eta", 1e-5, 1.0),
        "gamma": trial.suggest_loguniform("gamma", 1e-5, 1.0),
        "grow_policy": trial.suggest_categorical("grow_policy", ["depthwise", "lossguide"])
    }

    xgb_pipeline = Pipeline([("transform", col_transformer),
                        ("classifier", XGBClassifier(**param, random_state=42))])
    xgb_pipeline.fit(X_train, y_train)
    pred = xgb_pipeline.predict(X_test)
    accuracy = accuracy_score(y_test, pred)
    
    return accuracy

study_xgb = optuna.create_study(direction="maximize", sampler = TPESampler(seed = 42))
study_xgb.optimize(objective_xgb, timeout=300)

print("Mejores hiperparámetros para XGBClassifier: ", study_xgb.best_params)

best_params_xgb = study_xgb.best_params
optimized_xgb = XGBClassifier(**best_params_xgb, random_state=42)
optimized_xgb_pipeline = Pipeline([("transform", col_transformer), 
                                   ("classifier", optimized_xgb)])
optimized_xgb_pipeline.fit(X_train, y_train)
pred = optimized_xgb_pipeline.predict(X_test)

print("Optimized XGBClassifier")
print(classification_report(y_test, pred))
plot_pr_roc(y_test, optimized_xgb_pipeline.predict_proba(X_test)[:, 1])

[I 2024-07-17 17:32:01,070] A new study created in memory with name: no-name-f8aaf10e-90bd-4e3a-8f87-c571f7f61525
[I 2024-07-17 17:32:07,945] Trial 0 finished with value: 0.9901857075693465 and parameters: {'booster': 'gblinear', 'lambda': 0.09846738873614563, 'alpha': 0.0006026889128682511, 'max_depth': 2, 'eta': 1.951722464144947e-05, 'gamma': 0.21423021757741043, 'grow_policy': 'lossguide'}. Best is trial 0 with value: 0.9901857075693465.
[I 2024-07-17 17:32:14,285] Trial 1 finished with value: 0.9901857075693465 and parameters: {'booster': 'gblinear', 'lambda': 0.0011526449540315614, 'alpha': 0.0008111941985431928, 'max_depth': 2, 'eta': 0.00033205591037519585, 'gamma': 0.00420515645091387, 'grow_policy': 'depthwise'}. Best is trial 0 with value: 0.9901857075693465.
[I 2024-07-17 17:32:20,577] Trial 2 finished with value: 0.9901857075693465 and parameters: {'booster': 'gbtree', 'lambda': 0.006789053271698486, 'alpha': 0.019069966103000432, 'max_depth': 8, 'eta': 9.962513222055098e-

Mejores hiperparámetros para XGBClassifier:  {'booster': 'gblinear', 'lambda': 0.09846738873614563, 'alpha': 0.0006026889128682511, 'max_depth': 2, 'eta': 1.951722464144947e-05, 'gamma': 0.21423021757741043, 'grow_policy': 'lossguide'}
Optimized XGBClassifier
              precision    recall  f1-score   support

           0       0.99      1.00      1.00    117943
           1       0.00      0.00      0.00      1169

    accuracy                           0.99    119112
   macro avg       0.50      0.50      0.50    119112
weighted avg       0.98      0.99      0.99    119112



In [39]:
from zipfile import ZipFile
import os

X_t1 = pd.read_csv("X_t1", sep = ',')

def generateFiles(predict_data, clf_pipe):
    """Genera los archivos a subir en CodaLab

    Input
    ---------------
    predict_data: Dataframe con los datos de entrada a predecir
    clf_pipe: pipeline del clf

    Ouput
    ---------------
    archivo de txt
    """
    y_pred_clf = clf_pipe.predict_proba(predict_data)[:, 1]
    
    with open('./predictions.txt', 'w') as f:
        for item in y_pred_clf:
            f.write("%s\n" % item)

    with ZipFile('predictions.zip', 'w') as zipObj:
       zipObj.write('predictions.txt')
    os.remove('predictions.txt')

generateFiles(X_t1, optimized_xgb_pipeline)

#### **2.6 Interpretabilidad**

Utilización de SHAP , Anchors u otras herramientas de interpretabilidad, para ver la importancia de cada atributo en el modelo
final. Explicar o justificar la importancia de cada uno.


In [44]:
!pip install shap


[notice] A new release of pip is available: 24.0 -> 24.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [65]:
import shap

explainer = shap.TreeExplainer(optimized_xgb)
shap_values = explainer.shap_values(col_transformer.transform(X_test)) # Se calculan los SHAP values del modelo

# Obtener nombres de las características numéricas y categóricas transformada
cat_transformer = optimized_xgb_pipeline.named_steps['transform'].named_transformers_['cat']
cat_features = cat_transformer.get_feature_names_out(columnas_categoricas)
all_features = list(columnas_numericas) + list(cat_features)

KeyError: 'gbtree_model_param'

shap.summary_plot(shap_values, col_transformer.transform(X_test), feature_names=all_features)

In [19]:
# Se grafican los SHAP values para un cliente random
shap.initjs()
shap.force_plot(explainer.expected_value, shap_values[10], col_transformer.transform(X_test)[10], feature_names=all_features)

### 3. MLOPS

In [40]:
# lectura de archivos
X_t0 = pd.read_csv('X_t0', sep = ',')
X_t1 = pd.read_csv('X_t1', sep = ',')
X_t2 = pd.read_csv('X_t2', sep = ',')
y_t0 = pd.read_csv('y_t0', sep = ',')
y_t1 = pd.read_csv('y_t1', sep = ',')

#### 3.1 Monitoreo y Re-entrenamiento

El objetivo de este paso (monitoreo) es comprender la importancia de medir la consistencia de los datos y el desempeño de los modelos. Esta
práctica permite evitar potenciales problemas durante los pasos a producción, por lo que se debe observar constantemente los
modelos en funcionamiento.
* Implementar un sistema de monitoreo que permita verificar si existe data-drift entre los datos iniciales y los nuevos datos
entregados. Proponer un método basándose en la clase de monitoreo, fundamentando la decisión.
* Evaluación constante del rendimiento de los modelos en producción para detectar posibles desviaciones y anomalías

Con la variación y entrega de nuevos datos, un proyecto de data-science debe incluir este paso (re-entrenamiento). Sin embargo, entrenar con todos
los datos puede ser costoso. Es importante comprender que un re-entrenamiento puede ser caro y requiere herramientas
adecuadas.
* Diseñar y ejecutar estrategias de re-entrenamiento para mantener la precisión y relevancia de los modelos, utilizando
estrategias de partial fit.
* Automatizar el proceso de actualización de modelos basados en nuevos datos y feedback recibido a través de una función.
* Acompañar el re-entrenamiento de una etapa de optimización.
Podría serles útil la inicialización de modelos en base a pesos pasados. Mayor información la pueden encontrar en el siguiente link.

In [41]:
transform_pipeline = Pipeline([("transform", col_transformer)])

In [50]:
# train drift detector
from alibi_detect.cd import MMDDrift

# se genera un detector para X e y por separado
data_detector = MMDDrift(transform_pipeline.fit_transform(X_t0), backend='pytorch', p_val=.05)
target_detector = MMDDrift(y_t0.to_numpy(), backend='pytorch', p_val=.05)

# función utilitaria para detectar drift
def drift_detection(detector, new_data):

  '''
  Función que recibe un detector de alibi y nueva data.
  Devuelve un bool y p-value de test respecto a la presencia de drift
  '''

  output = detector.predict(new_data)['data']
  is_drift = bool(output['is_drift'])
  p_value = output['p_val']

  return is_drift, p_value

No GPU detected, fall back on CPU.


RuntimeError: The following operation failed in the TorchScript interpreter.
Traceback of TorchScript (most recent call last):
  File "c:\Users\benja\OneDrive\Escritorio\MDS7202\venv\lib\site-packages\alibi_detect\utils\pytorch\distance.py", line 29, in squared_pairwise_distance
    x2 = x.pow(2).sum(dim=-1, keepdim=True)
    y2 = y.pow(2).sum(dim=-1, keepdim=True)
    dist = torch.addmm(y2.transpose(-2, -1), x, y.transpose(-2, -1), alpha=-2).add_(x2)
           ~~~~~~~~~~~ <--- HERE
    return dist.clamp_min_(a_min)
RuntimeError: [enforce fail at alloc_cpu.cpp:114] data. DefaultCPUAllocator: not enough memory: you tried to allocate 1261119740168 bytes.


In [45]:
from scipy.stats import ks_2samp

def monitor_data_drift(reference_data, new_data):
    drift_report = {}
    for column in reference_data.columns:
        stat, p_value = ks_2samp(reference_data[column], new_data[column])
        drift_report[column] = {"KS Statistic": stat, "p-value": p_value}
    
    return drift_report

# Ejemplo de uso
reference_data = X_t0.copy()  # Datos de entrenamiento iniciales
new_data = X_t1.copy()  # Nuevos datos entrantes

drift_report = monitor_data_drift(reference_data, new_data)
print(drift_report)

{'DaysSinceJob': {'KS Statistic': 0.05068760688185059, 'p-value': 0.0}, 'CreditCap': {'KS Statistic': 0.08172848217233253, 'p-value': 0.0}, 'JobStatus': {'KS Statistic': 0.052100907896525106, 'p-value': 0.0}, 'Speed24h': {'KS Statistic': 0.3446949330903565, 'p-value': 0.0}, 'AliveSession': {'KS Statistic': 0.08202528412711879, 'p-value': 0.0}, 'BankSpots8w': {'KS Statistic': 0.012540458682519628, 'p-value': 1.4391536629127509e-22}, 'HustleMinutes': {'KS Statistic': 0.10375171258423616, 'p-value': 0.0}, 'RiskScore': {'KS Statistic': 0.218293470507282, 'p-value': 0.0}, 'AliasMatch': {'KS Statistic': 0.1142948700595881, 'p-value': 0.0}, 'DeviceEmails8w': {'KS Statistic': 0.018996926466165576, 'p-value': 3.080122437908987e-51}, 'CribStatus': {'KS Statistic': 0.12179553916273, 'p-value': 0.0}, 'LootMethod': {'KS Statistic': 0.0654932223473452, 'p-value': 0.0}, 'InfoSource': {'KS Statistic': 0.002058364689622505, 'p-value': 0.49764379280091386}, 'HustleMonth': {'KS Statistic': 1.0, 'p-value'

In [49]:
# drift detection
data_drift, p_value = drift_detection(data_detector, X_t1)
target_drift, p_value = drift_detection(target_detector, y_t1)

print('Data drift?', data_drift)
print('Target drift?', target_drift)

NameError: name 'data_detector' is not defined

#### 3.2 Integración de Trackeo en el Modelamiento e Interpretabilidad con MLFlow

Durante el modelamiento suceden muchas cosas, por lo que es relevante hacer un tracking de todos los elementos generados por
el modelo: métricas de desempeño, modelo, hiperparámetros, importancia de optimización, interpretabilidad, etc.
* Configurar MLFlow para rastrear experimentos, entrenamientos y versiones de modelos.
* Generar el tracking de los pasos más relevantes del modelo.

Resultados de los tracking de los modelos. Metricas de desempeño, modelo, hiperparámetros, importancia de optimización,
interpretabilidad, etc.

Para esta parte, le podría de ser utilidad el quickstart guide de MLFlow link, al igual que la clase

Nota: Es importante que al momento de generar el monitoreo, los nombres de sus experimentos sea descriptivos, de manera que
se pueda verificar de manera fácil que contiene cada modelo.


In [55]:
import mlflow 

def objective_xgb_mlflow(trial):
    param = {
        "verbosity": 0,
        "objective": "binary:logistic",
        "eval_metric": "logloss",
        "booster": trial.suggest_categorical("booster", ["gbtree", "gblinear", "dart"]),
        "lambda": trial.suggest_loguniform("lambda", 1e-4, 10),
        "alpha": trial.suggest_loguniform("alpha", 1e-4, 10),
        "max_depth": trial.suggest_int("max_depth", 1, 10),
        "eta": trial.suggest_loguniform("eta", 1e-5, 1.0),
        "gamma": trial.suggest_loguniform("gamma", 1e-5, 1.0),
        "grow_policy": trial.suggest_categorical("grow_policy", ["depthwise", "lossguide"])
    }

    xgb_pipeline = Pipeline([("transform", col_transformer),
                             ("classifier", XGBClassifier(**param))])
    
    with mlflow.start_run(nested=True, run_name=f"XGBoost con lr {param['eta']}"):
        xgb_pipeline.fit(X_train, y_train)
        pred = xgb_pipeline.predict(X_test)
        accuracy = accuracy_score(y_test, pred)

        mlflow.log_metric("accuracy", accuracy)
        
        mlflow.log_params(param)
        
        mlflow.sklearn.log_model(xgb_pipeline, "xgb_model")

    return accuracy

In [64]:
def main():
    mlflow.set_experiment("XGB Optimization Experiment")

    study = optuna.create_study(direction='maximize')
    study.optimize(objective_xgb_mlflow, timeout=600)

    best_trial = study.best_trial

    mlflow.log_params(best_trial.params)
    mlflow.log_metric("best_accuracy", best_trial.value)

    best_params = best_trial.params
    best_model = XGBClassifier(**best_params)
    
    pipeline = Pipeline([
        ("transform", col_transformer),
        ("classifier", best_model)
    ])
    pipeline.fit(X_train, y_train)
    
    plot_pr_roc(y_test, pipeline.predict_proba(X_test)[:, 1])
    
    print("Mejores hiperparámetros para XGBClassifier: ", best_params)
    preds = pipeline.predict(X_test)
    print("Optimized XGBClassifier")
    print(classification_report(y_test, preds))

In [66]:
if __name__ == "__main__":
    main()

[I 2024-07-15 19:16:21,896] A new study created in memory with name: no-name-9dbe8b07-6c43-4ddc-97f1-327111705561
[I 2024-07-15 19:16:33,742] Trial 0 finished with value: 0.9902108939485527 and parameters: {'booster': 'gbtree', 'lambda': 0.0006682499016204848, 'alpha': 0.02399884472371098, 'max_depth': 8, 'eta': 0.06613996077221254, 'gamma': 3.601824746451044e-05, 'grow_policy': 'depthwise'}. Best is trial 0 with value: 0.9902108939485527.
[I 2024-07-15 19:16:40,761] Trial 1 finished with value: 0.9901857075693465 and parameters: {'booster': 'gbtree', 'lambda': 0.0182033053023619, 'alpha': 0.0006172466484447044, 'max_depth': 4, 'eta': 5.856446939551842e-05, 'gamma': 0.043163128503976925, 'grow_policy': 'depthwise'}. Best is trial 0 with value: 0.9902108939485527.
[I 2024-07-15 19:22:51,432] Trial 2 finished with value: 0.9901857075693465 and parameters: {'booster': 'dart', 'lambda': 0.009549526297744089, 'alpha': 1.3039249301976334, 'max_depth': 3, 'eta': 0.00815910744716494, 'gamma': 

Mejores hiperparámetros para XGBClassifier:  {'booster': 'gbtree', 'lambda': 0.0006682499016204848, 'alpha': 0.02399884472371098, 'max_depth': 8, 'eta': 0.06613996077221254, 'gamma': 3.601824746451044e-05, 'grow_policy': 'depthwise'}
Optimized XGBClassifier
              precision    recall  f1-score   support

           0       0.99      1.00      1.00    117943
           1       0.54      0.02      0.03      1169

    accuracy                           0.99    119112
   macro avg       0.76      0.51      0.51    119112
weighted avg       0.99      0.99      0.99    119112



In [65]:
mlflow.end_run()

#### 3.3 Creación de API con Gradio y Posterior Dockerización

Nuestro objetivo es entregar este producto a un cliente final, por lo que debe ser fácilmente consultable a través de una
aplicación. Una buena alternativa web es Gradio.
* Crear una API que facilite la interfaz y la usabilidad de los modelos. Tienen completa libertad en esta parte, pero deben
generar una solución que permita realizar predicciones de manera sencilla. La API debe aceptar tanto la carga de archivos CSV
como el relleno de una planilla web con las variables del usuario.
* Dockerizar la API para asegurar su escalabilidad, portabilidad y despliegue eficiente en diferentes entornos.
Para la utilización de Docker, les podría ser de utilidad la cheatsheet de dockerlabs.


In [77]:
import gradio as gr

feature_names = X_train.columns.tolist()

def predict_from_csv(file):
    data = pd.read_csv(file.name)
    predictions = optimized_xgb_pipeline.predict(data)
    return predictions

def predict_from_input(*data):
    cat_data = data[:len(columnas_categoricas)]
    num_data = data[len(columnas_categoricas):]

    df = pd.DataFrame([num_data], columns=columnas_numericas)
    for cat_feature, value in zip(columnas_categoricas, cat_data):
        df[cat_feature] = value
    
    predictions = optimized_xgb_pipeline.predict(df)
    return predictions

with gr.Blocks() as demo:
    gr.Markdown("## Predicciones del Modelo XGB")
    with gr.TabItem("Cargar CSV"):
        csv_input = gr.File(label="Cargar archivo CSV")
        csv_output = gr.Textbox(label="Predicciones")
        csv_button = gr.Button("Predecir")
        csv_button.click(fn=predict_from_csv, inputs=csv_input, outputs=csv_output)
    
    with gr.TabItem("Rellenar Planilla"): # Hay que colocar valores válidos para las variables categóricas
        inputs = [gr.Textbox(label=feature) for feature in columnas_categoricas] + \
                 [gr.Number(label=feature) for feature in columnas_numericas]
        manual_output = gr.Textbox(label="Predicciones")
        manual_button = gr.Button("Predecir")
        manual_button.click(fn=predict_from_input, inputs=inputs, outputs=manual_output)

demo.launch()

Running on local URL:  http://127.0.0.1:7865

To create a public link, set `share=True` in `launch()`.


Traceback (most recent call last):
  File "c:\Users\benja\OneDrive\Escritorio\MDS7202\venv\lib\site-packages\gradio\queueing.py", line 536, in process_events
    response = await route_utils.call_process_api(
  File "c:\Users\benja\OneDrive\Escritorio\MDS7202\venv\lib\site-packages\gradio\route_utils.py", line 276, in call_process_api
    output = await app.get_blocks().process_api(
  File "c:\Users\benja\OneDrive\Escritorio\MDS7202\venv\lib\site-packages\gradio\blocks.py", line 1897, in process_api
    result = await self.call_function(
  File "c:\Users\benja\OneDrive\Escritorio\MDS7202\venv\lib\site-packages\gradio\blocks.py", line 1483, in call_function
    prediction = await anyio.to_thread.run_sync(
  File "c:\Users\benja\OneDrive\Escritorio\MDS7202\venv\lib\site-packages\anyio\to_thread.py", line 56, in run_sync
    return await get_async_backend().run_sync_in_worker_thread(
  File "c:\Users\benja\OneDrive\Escritorio\MDS7202\venv\lib\site-packages\anyio\_backends\_asyncio.py", li

#### 3.4 Canalizaciones Productivas

Esta sección es pertinente a la entrega final del proyecto, por lo que se develara en el enunciado de la parte 3.